## Лабораторная работа №6

### Задание 1
Провести классификацию найденного датасета, методами CatBoost . В формате Markdown написать пояснения. Объяснить почему были выбраны именно такие гиперпараметры, была ли перекрестная проверка, и т.д.

### Выполнение работы:

Если не установлен модуль CatBoost необходимо в консоль ввести команду pip install catboost

#### Шаг 1. Загрузка датасета

In [1]:
import pandas as pd
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler
from catboost import CatBoostClassifier
from sklearn.model_selection import GridSearchCV
from sklearn.metrics import accuracy_score, classification_report
from tqdm import tqdm

# Загрузка датасета
file_path = "../Dataset.xls"
data = pd.read_excel(file_path)

data

ID  LIMIT_BAL  SEX  EDUCATION  MARRIAGE  AGE  PAY_0  PAY_2  PAY_3   
0          1      20000    2          2         1   24      2      2     -1  \
1          2     120000    2          2         2   26     -1      2      0   
2          3      90000    2          2         2   34      0      0      0   
3          4      50000    2          2         1   37      0      0      0   
4          5      50000    1          2         1   57     -1      0     -1   
...      ...        ...  ...        ...       ...  ...    ...    ...    ...   
29995  29996     220000    1          3         1   39      0      0      0   
29996  29997     150000    1          3         2   43     -1     -1     -1   
29997  29998      30000    1          2         2   37      4      3      2   
29998  29999      80000    1          3         1   41      1     -1      0   
29999  30000      50000    1          2         1   46      0      0      0   

       PAY_4  ...  BILL_AMT4  BILL_AMT5  BILL_AMT6  PAY_AMT1  PAY_AMT2   
0         -1  ...          0          0          0         0       689  \
1          0  ...       3272       3455       3261         0      1000   
2          0  ...      14331      14948      15549      1518      1500   
3          0  ...      28314      28959      29547      2000      2019   
4          0  ...      20940      19146      19131      2000     36681   
...      ...  ...        ...        ...        ...       ...       ...   
29995      0  ...      88004      31237      15980      8500     20000   
29996     -1  ...       8979       5190          0      1837      3526   
29997     -1  ...      20878      20582      19357         0         0   
29998      0  ...      52774      11855      48944     85900      3409   
29999      0  ...      36535      32428      15313      2078      1800   

       PAY_AMT3  PAY_AMT4  PAY_AMT5  PAY_AMT6  default payment next month  
0             0         0         0         0                           1  
1          1000      1000         0      2000                           1  
2          1000      1000      1000      5000                           0  
3          1200      1100      1069      1000                           0  
4         10000      9000       689       679                           0  
...         ...       ...       ...       ...                         ...  
29995      5003      3047      5000      1000                           0  
29996      8998       129         0         0                           0  
29997     22000      4200      2000      3100                           1  
29998      1178      1926     52964      1804                           1  
29999      1430      1000      1000      1000                           1  

[30000 rows x 25 columns]

#### Шаг 2. Разделение данных и нормализация

In [2]:
# Разделение на признаки (X) и целевую переменную (y)
X = data.drop('default payment next month', axis=1)
y = data['default payment next month']

# Разделение данных на тренировочный и тестовый наборы
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

# Масштабирование признаков (нормализация)
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)

#### Шаг 3. Метод CatBoost
Гиперпараметры:

depth: Этот параметр определяет глубину дерева. Увеличение значения этого параметра увеличивает сложность модели, что может привести к более точной подгонке к тренировочным данным, но также увеличивает риск переобучения.
learning_rate: Определяет скорость обучения модели. Этот параметр контролирует величину, на которую обновляются веса модели при каждой итерации. Более низкие значения могут способствовать стабильному обучению, но могут потребовать большего количества итераций для достижения оптимальной точности.
l2_leaf_reg: Этот параметр отвечает за коэффициент регуляризации L2 (Ridge). Он контролирует сложность модели, ограничивая веса и предотвращая переобучение. Большие значения могут уменьшить сложность модели, но могут также уменьшить её точность на тренировочных данных.

In [3]:
# Определение параметров для CatBoost
param_grid_catboost = {
    'depth': [1, 4, 7, 10],
    'learning_rate': [0.01, 0.1, 1],
    'l2_leaf_reg': [1, 3, 5, 9],
    'iterations': [100, 200,],
    'depth': [0, 3, 6],
    'loss_function': ['MultiClass', 'Logloss']
}

In [4]:
# Создание модели CatBoost
catboost = CatBoostClassifier()

# Подбор оптимальных параметров с помощью перекрестной проверки для CatBoost
grid_search_catboost = GridSearchCV(catboost, param_grid_catboost, refit=True, verbose=3, cv=5)
grid_search_catboost.fit(X_train_scaled, y_train)

# Получение лучших параметров для CatBoost
best_params_catboost = grid_search_catboost.best_params_
best_score_catboost = grid_search_catboost.best_score_

Fitting 5 folds for each of 144 candidates, totalling 720 fits
0:	learn: 0.6900677	total: 148ms	remaining: 14.6s
1:	learn: 0.6870494	total: 149ms	remaining: 7.29s
2:	learn: 0.6840908	total: 150ms	remaining: 4.84s
3:	learn: 0.6811907	total: 150ms	remaining: 3.61s
4:	learn: 0.6783477	total: 151ms	remaining: 2.87s
5:	learn: 0.6755605	total: 152ms	remaining: 2.38s
6:	learn: 0.6728280	total: 153ms	remaining: 2.03s
7:	learn: 0.6701487	total: 154ms	remaining: 1.77s
8:	learn: 0.6675217	total: 155ms	remaining: 1.56s
9:	learn: 0.6649458	total: 156ms	remaining: 1.4s
10:	learn: 0.6624198	total: 156ms	remaining: 1.26s
11:	learn: 0.6599426	total: 157ms	remaining: 1.15s
12:	learn: 0.6575132	total: 158ms	remaining: 1.06s
13:	learn: 0.6551307	total: 159ms	remaining: 975ms
14:	learn: 0.6527938	total: 160ms	remaining: 904ms
15:	learn: 0.6505018	total: 160ms	remaining: 842ms
16:	learn: 0.6482537	total: 161ms	remaining: 788ms
17:	learn: 0.6460485	total: 162ms	remaining: 738ms
18:	learn: 0.6438853	total: 16

#### Шаг 4. Вывод результатов

In [5]:
test_score = grid_search_catboost.score(X_test_scaled, y_test)
print("Лучшие параметры для CatBoost:", best_params_catboost)
print("Лучший результат (точность) для CatBoost:", best_score_catboost)
print("Точность на тестовом наборе данных:", test_score)

best_model = grid_search_catboost.best_estimator_
predictions = best_model.predict(X_test_scaled)

# Отчет по классификации
print("\nОтчет по классификации:")
print(classification_report(y_test, predictions))

Лучшие параметры для CatBoost: {'depth': 3, 'iterations': 100, 'l2_leaf_reg': 9, 'learning_rate': 0.1, 'loss_function': 'Logloss'}
Лучший результат (точность) для CatBoost: 0.8216666666666667
Точность на тестовом наборе данных: 0.8191666666666667

Отчет по классификации:
              precision    recall  f1-score   support

           0       0.84      0.95      0.89      4687
           1       0.66      0.36      0.46      1313

    accuracy                           0.82      6000
   macro avg       0.75      0.65      0.68      6000
weighted avg       0.80      0.82      0.80      6000

